# Audio Processing with Transformers


In this notebook, we will use the Hugging Face Transformers library to process audio data.


## Zero-Shot Classification


Let's start with a problem already seen in computer vision: zero-shot classification. This involves determining the origin of an audio clip without training on specific categories.


### Implementation


For this, we use the ESC-50 dataset (ashraq/esc50), which contains 5-second recordings across 50 different categories.
To download it, we use the Hugging Face datasets library:


In [1]:
from datasets import load_dataset
from transformers import pipeline
from IPython.display import Audio as IPythonAudio

/home/aquilae/anaconda3/envs/dev/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
dataset = load_dataset("ashraq/esc50",split="train[0:10]")

We can observe the metadata of the audio clip. The *sampling_rate* is particularly important. You need to ensure it matches that of the model's training data.


In [6]:
audio_sample = dataset[0]
audio_sample

{'filename': '1-100038-A-14.wav',
 'fold': 1,
 'target': 14,
 'category': 'chirping_birds',
 'esc10': False,
 'src_file': 100038,
 'take': 'A',
 'audio': {'path': None,
  'array': array([-0.01184082, -0.10336304, -0.14141846, ...,  0.06985474,
          0.04049683,  0.00274658]),
  'sampling_rate': 44100}}

You can listen to the audio clip (be careful not to turn up your computer volume too high) with IPython.


In [7]:
IPythonAudio(audio_sample["audio"]["array"],rate=audio_sample["audio"]["sampling_rate"])

It's time to use the Hugging Face pipeline to retrieve our model.
We use the CLAP model from LAION-AI (laion/clap-htsat-unfused).


In [9]:
audio_zero_shot = pipeline(task="zero-shot-audio-classification",model="laion/clap-htsat-unfused")

Let's check the model's *sampling rate* to see if it matches our data.


In [14]:
print("Sampling rate du modèle : ",audio_zero_shot.feature_extractor.sampling_rate)
print("Sampling rate de notre extrait : ",audio_sample["audio"]["sampling_rate"])

Sampling rate du modèle :  48000
Sampling rate de notre extrait :  44100


We need to modify our dataset's *sampling rate* to match the model.


In [16]:
from datasets import Audio
dataset = dataset.cast_column("audio",Audio(sampling_rate=48_000))
audio_sample = dataset[0]
print("Sampling rate de notre extrait : ",audio_sample["audio"]["sampling_rate"])

Sampling rate de notre extrait :  48000


Now that the clips and model are synchronized, we can proceed with classification.
We will propose candidate labels (similar to the CLIP model in vision).


In [18]:
candidate_labels = ["Sound of a dog","Sound of cat"]
outputs=audio_zero_shot(audio_sample["audio"]["array"],candidate_labels=candidate_labels)
print("Score de "+candidate_labels[0],outputs[0]["score"])
print("Score de "+candidate_labels[1],outputs[1]["score"])

Score de Sound of a dog 0.9805886149406433
Score de Sound of cat 0.019411340355873108


The model can identify that the audio clip is a dog bark and not a cat meow.
You can test with your own audio clips or with other clips from the dataset.


## Automatic Speech Recognition


Automatic speech recognition involves transcribing speech into text. This is useful for voice note-taking, activating smart devices ('Ok Google', 'Hey Siri'), and many other applications.


### Implementation


In this example, we use the LibriSpeech ASR corpus, which contains approximately 1000 hours of English speech.


In [19]:
from datasets import load_dataset
dataset = load_dataset("librispeech_asr",split="train.clean.100",streaming=True,trust_remote_code=True)

In [25]:
example = next(iter(dataset))
example

{'file': '374-180298-0000.flac',
 'audio': {'path': '374-180298-0000.flac',
  'array': array([ 7.01904297e-04,  7.32421875e-04,  7.32421875e-04, ...,
         -2.74658203e-04, -1.83105469e-04, -3.05175781e-05]),
  'sampling_rate': 16000},
 'text': 'CHAPTER SIXTEEN I MIGHT HAVE TOLD YOU OF THE BEGINNING OF THIS LIAISON IN A FEW LINES BUT I WANTED YOU TO SEE EVERY STEP BY WHICH WE CAME I TO AGREE TO WHATEVER MARGUERITE WISHED',
 'speaker_id': 374,
 'chapter_id': 180298,
 'id': '374-180298-0000'}

In [24]:
from IPython.display import Audio as IPythonAudio

IPythonAudio(example["audio"]["array"],rate=example["audio"]["sampling_rate"])

We will use the Whisper model (distil-whisper/distil-small.en) from OpenAI, designed for English speech recognition. This is a reduced version of the original model.
Let's now build our Hugging Face pipeline.


In [27]:
reco_parole = pipeline(task="automatic-speech-recognition",model="distil-whisper/distil-small.en")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [30]:
print("Sampling rate du modèle : ",reco_parole.feature_extractor.sampling_rate)
print("Sampling rate de notre extrait : ",example['audio']['sampling_rate'])

Sampling rate du modèle :  16000
Sampling rate de notre extrait :  16000


The *sampling rates* are identical, so there's no need to modify anything.


In [37]:
output=reco_parole(example["audio"]["array"])
print("Texte transcrit : ",output['text'])
print("Texte de base : ",example["text"].lower())

Texte transcrit :   Chapter 16 I might have told you of the beginning of this liaison in a few lines, but I wanted you to see every step by which we came. I too agree to whatever Marguerite wished.
Texte de base :  chapter sixteen i might have told you of the beginning of this liaison in a few lines but i wanted you to see every step by which we came i to agree to whatever marguerite wished


As you can see, the transcription is quite faithful to the original.


## Text-to-Speech Conversion


This task is the opposite of the previous one. Here, we provide text as input, and the model generates audio of a person saying that text.


### Implementation


We use the vits model from kakao-enterprise (kakao-enterprise/vits-ljs).


In [5]:
text_parole = pipeline("text-to-speech", model="kakao-enterprise/vits-ljs")

Some weights of the model checkpoint at kakao-enterprise/vits-ljs were not used when initializing VitsModel: ['flow.flows.0.wavenet.in_layers.0.weight_g', 'flow.flows.0.wavenet.in_layers.0.weight_v', 'flow.flows.0.wavenet.in_layers.1.weight_g', 'flow.flows.0.wavenet.in_layers.1.weight_v', 'flow.flows.0.wavenet.in_layers.2.weight_g', 'flow.flows.0.wavenet.in_layers.2.weight_v', 'flow.flows.0.wavenet.in_layers.3.weight_g', 'flow.flows.0.wavenet.in_layers.3.weight_v', 'flow.flows.0.wavenet.res_skip_layers.0.weight_g', 'flow.flows.0.wavenet.res_skip_layers.0.weight_v', 'flow.flows.0.wavenet.res_skip_layers.1.weight_g', 'flow.flows.0.wavenet.res_skip_layers.1.weight_v', 'flow.flows.0.wavenet.res_skip_layers.2.weight_g', 'flow.flows.0.wavenet.res_skip_layers.2.weight_v', 'flow.flows.0.wavenet.res_skip_layers.3.weight_g', 'flow.flows.0.wavenet.res_skip_layers.3.weight_v', 'flow.flows.1.wavenet.in_layers.0.weight_g', 'flow.flows.1.wavenet.in_layers.0.weight_v', 'flow.flows.1.wavenet.in_layers.

Let's try generating a sentence in French.


In [6]:
text = """Ce cours de deep learning est incroyable."""
generated_parole = text_parole(text)
IPythonAudio(generated_parole["audio"][0],rate=generated_parole["sampling_rate"])

As you can see, the result is not satisfactory because the model is trained on English data. If you want to generate French, you'll need to find a suitable model.
Let's try now with a sentence in English:


In [7]:
text = """This deep learning course is fantastic."""
generated_parole = text_parole(text)
IPythonAudio(generated_parole["audio"][0],rate=generated_parole["sampling_rate"])

That's much better!


**Note 1**: You can also combine multiple models. For example, you take your French sentence, translate it to English, and then generate the corresponding audio.
**Note 2**: If you want to generate sound (music, ambiance, noise, etc.) that is not speech, you should look at the Text-to-Audio category on Hugging Face.
